Những tasks cần làm được đánh dấu bằng Markdown
Dữ liệu cần xử lý (thô): jobs_data.csv
Dữ liệu đã xử lý qua 1 tý : cleaned.csv
Dữ liệu B (dành cho trường hợp xử lý bên A không được): jobs_data_extracted_2.csv (không được sửa, đây là file cũ t làm nhưng xóa rồi)
Làm việc chính với cột Salary, không phải (Max Salary), (Min Salary)

In [ ]:
import pandas as pd
# "Job Title": job.get('job_title', 'Not Available'),
#                     "Job Score": job.get('job_apply_quality_score','Not Available'),
#                     "Job Experience Required": job.get('required_experience_in_months', 'Not Available'), 
#                     "Postgraduate degree": job.get('postgraduate_degree',False),
#                     "Job Skills Required": job.get('job_required_skills','Not Available'),
#                     "Job Location": f"{job.get('job_city', 'Not Available')} {job.get('job_state', 'Not Available')} {job.get('job_country', 'Not Available')}",
#                     "Job Description": job.get('job_description', 'Not Available'),
#                     "Job Min Salary": job.get('job_min_salary', 'Not Available'),
#                     "Job Max Salary": job.get('job_max_salary', 'Not Available'),
#                     "Job Apply Link": job.get('job_apply_link', 'Not Available')

In [6]:
import requests
import pandas as pd

# URL của API
url = "https://jsearch.p.rapidapi.com/search"

# Tham số truy vấn
querystring = {
    "query":" developer",  
    "page": "1",  
    "country": "us", 
    "date_posted": "all"  
}


headers = {
    "x-rapidapi-key": "ae3c3e2a3bmsh004bd7ff719d4e1p1bc770jsnb14e370b91f8",  # API key của bạn
    "x-rapidapi-host": "jsearch.p.rapidapi.com"
}

# Danh sách lưu trữ dữ liệu công việc
jobs_list = []


page = 1
max_pages = 60

while page <= max_pages:
    
    querystring["page"] = str(page)

    response = requests.get(url, headers=headers, params=querystring)
    
    print(f"Trang {page} - Status Code: {response.status_code}")

    if response.status_code == 200:
        data = response.json() 
        print(f"Response JSON - Page {page}:", data)  
        print("Request Parameters:", data.get("parameters", {}))
        jobs_data = data.get("data", [])
        
        if jobs_data:
            print(f"Số lượng công việc: {len(jobs_data)}")
            for job in jobs_data:
                # Lấy thông tin công việc và thêm vào danh sách
                jobs_list.append({
                    "Job Title": job.get('job_title', 'Not Available'),
                    "Job Score": job.get('job_apply_quality_score','Not Available'),
                    "Job Experience Required": job.get('required_experience_in_months', 'Not Available'), 
                    "Postgraduate degree": job.get('postgraduate_degree',False),
                    "Job Skills Required": job.get('Qualifications','Not Available'),
                    "Job Location": f"{job.get('job_city', 'Not Available')} {job.get('job_state', 'Not Available')} {job.get('job_country', 'Not Available')}",
                    "Job Description": job.get('job_description', 'Not Available'),
                    "Job Min Salary": job.get('job_min_salary', 'Not Available'),
                    "Job Max Salary": job.get('job_max_salary', 'Not Available'),
                    "Year": job.get('job_posted_at_datetime_utc')
                })
        else:
            print("Không có công việc nào trong phản hồi.")
    else:
        print(f"Lỗi khi tải dữ liệu từ API: {response.status_code}")
        print(f"Chi tiết lỗi: {response.text}")
   
    page += 1

if jobs_list:
    # Chuyển dữ liệu thành DataFrame
    df = pd.DataFrame(jobs_list)
    
    # Lưu DataFrame vào file CSV
    df.to_csv('jobs_data.csv', index=False, encoding='utf-8')
    print(f"Dữ liệu đã được lưu vào file jobs_data.csv.")
else:
    print("Không có dữ liệu để lưu.")


Trang 1 - Status Code: 200
Response JSON - Page 1: {'status': 'OK', 'request_id': '502d7177-ea31-4e61-a0c1-33d969b95cff', 'parameters': {'query': 'developer', 'page': 1, 'num_pages': 1, 'date_posted': 'all', 'country': 'us', 'language': 'en'}, 'data': [{'job_id': 'mUyBEGFxEucJl-K7AAAAAA==', 'employer_name': 'Artech Information Systems', 'employer_logo': None, 'employer_website': 'https://www.artech.com', 'employer_company_type': None, 'employer_linkedin': None, 'job_publisher': 'Clearance Jobs', 'job_employment_type': 'CONTRACTOR', 'job_employment_types': ['CONTRACTOR', 'CONTRACTOR'], 'job_employment_type_text': 'Contractor', 'job_title': '.Net Developer Jobs', 'job_apply_link': 'https://www.clearancejobs.com/jobs/8067331/net-developer?utm_campaign=google_jobs_apply&utm_source=google_jobs_apply&utm_medium=organic', 'job_apply_is_direct': True, 'job_apply_quality_score': None, 'apply_options': [{'publisher': 'Clearance Jobs', 'apply_link': 'https://www.clearancejobs.com/jobs/8067331/net

Extract năm kinh nghiệm, kỹ năng cần có

In [3]:
import pandas as pd
import re

In [116]:
df = pd.read_csv('jobs_data.csv')
df

Job Title  Job Score  \
0                                  .Net Developer Jobs        NaN   
1                                       .NET Developer        NaN   
2                          MS Power Platform Developer        NaN   
3                            Data Developer/ Team Lead        NaN   
4                   CBT Developer w active TS/SCI Poly        NaN   
..                                                 ...        ...   
432  SOFTWARE DEVELOPER (CTV) - (Bright Script/Reac...        NaN   
433                                     Java Developer        NaN   
434         Website Developer (.60-1.0 FTE) #2025-38A5        NaN   
435                    Junior Level Software Developer        NaN   
436                                      Web Developer        NaN   

    Job Experience Required  Postgraduate degree Job Skills Required  \
0             Not Available                False       Not Available   
1             Not Available                False       Not Available   
2             Not Available                False       Not Available   
3             Not Available                False       Not Available   
4             Not Available                False       Not Available   
..                      ...                  ...                 ...   
432           Not Available                False       Not Available   
433           Not Available                False       Not Available   
434           Not Available                False       Not Available   
435           Not Available                False       Not Available   
436           Not Available                False       Not Available   

    Job Location                                    Job Description  \
0     None DC US  Client is seeking a senior-mid level .Net deve...   
1     None VA US  As the .NET Developer you will be apart of a t...   
2     None VA US  Description\n\nLeidos currently has an opening...   
3     None DC US  Required Qualifications:\n• 5 years with BS/BA...   
4     None MD US  Description\n\nLooking for a rewarding career ...   
..           ...                                                ...   
432   None GA US  About Gray Media:\n\nGray Media is a leading m...   
433   None MI US  About Us\n\nSynergistic IT is a full-service s...   
434   None NY US  Application Deadline\n\nDecember 13, 2024 (or ...   
435   None TX US  Since 2010 SynergisticIT has helped Jobseekers...   
436   None LA US  Please note that this position is based on our...   

     Job Min Salary  Job Max Salary                      Year  
0               NaN             NaN  2024-11-22T00:00:00.000Z  
1               NaN             NaN                       NaN  
2               NaN             NaN  2024-11-21T00:00:00.000Z  
3               NaN             NaN  2024-10-23T00:00:00.000Z  
4               NaN             NaN  2024-11-21T00:00:00.000Z  
..              ...             ...                       ...  
432             NaN             NaN                       NaN  
433             NaN             NaN                       NaN  
434             NaN             NaN  2024-11-15T00:00:00.000Z  
435             NaN             NaN                       NaN  
436             NaN             NaN  2024-11-15T00:00:00.000Z  

[437 rows x 10 columns]

In [121]:
df = df.drop_duplicates()

In [117]:

salary_regex = r"(\$\d{1,3}(?:,\d{3})*(?:\.\d+)?(?:k|K)?(?:\s*(USD)?)?)"

experience_regex = r"(\d+\+?)\s*(?:years?|yrs?|year)"

def extract_salary_and_experience(row):

    if pd.isna(row['Job Min Salary']) and pd.isna(row['Job Max Salary']):
        # Trích xuất lương từ Job Description
        salary_match = re.search(salary_regex, row['Job Description'])
        if salary_match:
            salary = salary_match.group(0)
            return salary 
        else:
            return None  
    else:
       
        min_salary = row['Job Min Salary']
        max_salary = row['Job Max Salary']
        
        
        if isinstance(min_salary, str) and 'k' in min_salary.lower():
            min_salary = float(min_salary.replace('$', '').replace(',', '').replace('k', '').strip()) * 1000
        if isinstance(max_salary, str) and 'k' in max_salary.lower():
            max_salary = float(max_salary.replace('$', '').replace(',', '').replace('k', '').strip()) * 1000

        if min_salary is not None and max_salary is not None:
           
            return (min_salary + max_salary) / 2
        return None 
def extract_experience(row):

    experience_match = re.search(experience_regex, row['Job Description'])
    if experience_match:
        return experience_match.group(0)  
    return None  
df['Salary'] = df.apply(extract_salary_and_experience, axis=1)
df['Experience'] = df.apply(extract_experience, axis=1)

df['Salary'] = df['Salary'].replace({'\$': '', ',': '', 'k': '000'}, regex=True) 
df['Salary'] = pd.to_numeric(df['Salary'], errors='coerce') 


df_na_salary = df[df['Salary'].isna()]

print(df_na_salary[['Job Title', 'Salary']]) 




                                             Job Title  Salary
0                                  .Net Developer Jobs     NaN
1                                       .NET Developer     NaN
3                            Data Developer/ Team Lead     NaN
6                            Expert Software Developer     NaN
13                               Application Developer     NaN
..                                                 ...     ...
432  SOFTWARE DEVELOPER (CTV) - (Bright Script/Reac...     NaN
433                                     Java Developer     NaN
434         Website Developer (.60-1.0 FTE) #2025-38A5     NaN
435                    Junior Level Software Developer     NaN
436                                      Web Developer     NaN

[222 rows x 2 columns]


<>:39: SyntaxWarning: invalid escape sequence '\$'
<>:39: SyntaxWarning: invalid escape sequence '\$'
C:\Users\Admin\AppData\Local\Temp\ipykernel_13904\2864670202.py:39: SyntaxWarning: invalid escape sequence '\$'
  df['Salary'] = df['Salary'].replace({'\$': '', ',': '', 'k': '000'}, regex=True)


In [118]:
df = df.drop('Job Max Salary',axis =1)
df = df.drop('Job Min Salary',axis =1)

In [119]:
df['Salary']

0          NaN
1          NaN
2      81250.0
3          NaN
4      78000.0
        ...   
432        NaN
433        NaN
434        NaN
435        NaN
436        NaN
Name: Salary, Length: 437, dtype: float64

Chuẩn hóa cột Salary

Xử lý salary (nhập tay) không extract được

In [32]:
df.dtypes

Job Title                   object
Job Score                  float64
Job Experience Required     object
Postgraduate degree           bool
Job Skills Required         object
Job Location                object
Job Description             object
Year                        object
Salary                     float64
Experience                  object
dtype: object

Xử lý những dữ liệu bất thường/ không extract được

In [122]:
df[df['Salary'] < 10]

Job Title  Job Score Job Experience Required  \
69               API Developer        NaN           Not Available   
152  IT Developer - Dublin, CA        NaN           Not Available   

     Postgraduate degree Job Skills Required Job Location  \
69                 False       Not Available   None GA US   
152                False       Not Available   None CA US   

                                       Job Description  \
69   Position Title: API Developer\n\nlocation: Alp...   
152  About Us\n\nThe Save Mart Companies operates 1...   

                         Year  Salary Experience  
69   2024-11-19T00:00:00.000Z     3.0   3+ years  
152  2024-11-09T00:00:00.000Z     5.0   70 years

$70,000.00 - $75,000.00 /per year
dòng 389 lương là  $115,764.00 - 119,017.00


In [123]:
df['Salary'][152] = (70000+75000)/2
df['Salary'][69] = (115764+119017)/2

C:\Users\Admin\AppData\Local\Temp\ipykernel_13904\571119086.py:1: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  df['Salary'][152] = (70000+75000)/2
C:\Users\Admin\AppData\Local\Temp\ipykernel_13904\571119086.py:2: FutureWarning: ChainedAssig

Giả sử mỗi tuần họ làm việc bao nhiêu giờ ?

In [124]:
df['Job Title']

0                                    .Net Developer Jobs
1                                         .NET Developer
2                            MS Power Platform Developer
3                              Data Developer/ Team Lead
4                     CBT Developer w active TS/SCI Poly
                             ...                        
409    C#.NET Developer w/ React Exp (Mid-Sr) - Remot...
410                             Web Developer I - 525281
416    Adjunct Faculty Non-Instructional Course Devel...
418    Developer in Test II - Core Enterprise Data an...
419                             UI Developer - Plano, TX
Name: Job Title, Length: 212, dtype: object

In [39]:
keywords = {
    'Frontend Development': ['Frontend Web Developer', 'Frontend Developer', 'Web/Frontend Developer'],
    'Web Development': ['Full Stack Web Developer', 'Web Developer', 'Web', 'Website'],
    'Software Development': ['Python Developer', 'Java Developer', 'Full Stack Developer','Software'],
    'Data Science': ['Data Scientist', 'Machine Learning', 'Data'],
    'DevOps': ['DevOps']
}

sorted_keywords = {
    group: sorted(terms, key=len, reverse=True) for group, terms in keywords.items()
}

def classify_job_title(job_title):
    job_title = job_title.lower() 
    for group, terms in sorted_keywords.items():
        for term in terms:
            if term.lower() in job_title:  
                return group
    return 'Software Development' 
df['Job Group'] = df['Job Title'].apply(classify_job_title)


In [126]:
df['Job Group'].unique()

array(['Other', 'Data Science', 'Software Development', 'Web Development',
       'Frontend Development', 'DevOps'], dtype=object)

In [127]:
import re

In [129]:
df.loc[df['Salary'] <= 500, 'Salary'] = df[df['Salary'] <= 500]['Salary'] * 2000

In [131]:
df['Experience'] = df['Experience'].apply(lambda x: int(re.findall(r'\d+', str(x))[0]) if re.findall(r'\d+', str(x)) else 0)


In [132]:
df

Job Title  Job Score  \
0                                  .Net Developer Jobs        NaN   
1                                       .NET Developer        NaN   
2                          MS Power Platform Developer        NaN   
3                            Data Developer/ Team Lead        NaN   
4                   CBT Developer w active TS/SCI Poly        NaN   
..                                                 ...        ...   
409  C#.NET Developer w/ React Exp (Mid-Sr) - Remot...        NaN   
410                           Web Developer I - 525281        NaN   
416  Adjunct Faculty Non-Instructional Course Devel...        NaN   
418  Developer in Test II - Core Enterprise Data an...        NaN   
419                           UI Developer - Plano, TX        NaN   

    Job Experience Required  Postgraduate degree Job Skills Required  \
0             Not Available                False       Not Available   
1             Not Available                False       Not Available   
2             Not Available                False       Not Available   
3             Not Available                False       Not Available   
4             Not Available                False       Not Available   
..                      ...                  ...                 ...   
409           Not Available                False       Not Available   
410           Not Available                False       Not Available   
416           Not Available                False       Not Available   
418           Not Available                False       Not Available   
419           Not Available                False       Not Available   

    Job Location                                    Job Description  \
0     None DC US  Client is seeking a senior-mid level .Net deve...   
1     None VA US  As the .NET Developer you will be apart of a t...   
2     None VA US  Description\n\nLeidos currently has an opening...   
3     None DC US  Required Qualifications:\n• 5 years with BS/BA...   
4     None MD US  Description\n\nLooking for a rewarding career ...   
..           ...                                                ...   
409   None PA US  As the largest online distributor of restauran...   
410   None AL US  Pay Grade/Pay Range: Minimum: $48,600 - Midpoi...   
416   None CA US  Adjunct Faculty Non-Instructional Course Devel...   
418   None WA US  Company Description\n\n“We’re not in the shipp...   
419   None TX US  Position : UI Developer\nLocation : Plano, TX\...   

                         Year    Salary  Experience        Job Group  
0    2024-11-22T00:00:00.000Z       NaN           6            Other  
1                         NaN       NaN           0            Other  
2    2024-11-21T00:00:00.000Z   81250.0           4            Other  
3    2024-10-23T00:00:00.000Z       NaN           5     Data Science  
4    2024-11-21T00:00:00.000Z   78000.0           8            Other  
..                        ...       ...         ...              ...  
409  2024-11-11T00:00:00.000Z       NaN           4            Other  
410  2024-11-17T00:00:00.000Z   48600.0           0  Web Development  
416                       NaN   68000.0           0            Other  
418                       NaN  100000.0           4     Data Science  
419                       NaN       NaN           0            Other  

[212 rows x 11 columns]

In [133]:
df[df['Salary'].isna()]

Job Title  Job Score  \
0                                  .Net Developer Jobs        NaN   
1                                       .NET Developer        NaN   
3                            Data Developer/ Team Lead        NaN   
6                            Expert Software Developer        NaN   
13                               Application Developer        NaN   
..                                                 ...        ...   
344          Front End React Developer (TS/SCI w/Poly)        NaN   
396                         Web Developer (Costa Rica)        NaN   
407                               Angular 2+ Developer        NaN   
409  C#.NET Developer w/ React Exp (Mid-Sr) - Remot...        NaN   
419                           UI Developer - Plano, TX        NaN   

    Job Experience Required  Postgraduate degree Job Skills Required  \
0             Not Available                False       Not Available   
1             Not Available                False       Not Available   
3             Not Available                False       Not Available   
6             Not Available                False       Not Available   
13            Not Available                False       Not Available   
..                      ...                  ...                 ...   
344           Not Available                False       Not Available   
396           Not Available                False       Not Available   
407           Not Available                False       Not Available   
409           Not Available                False       Not Available   
419           Not Available                False       Not Available   

    Job Location                                    Job Description  \
0     None DC US  Client is seeking a senior-mid level .Net deve...   
1     None VA US  As the .NET Developer you will be apart of a t...   
3     None DC US  Required Qualifications:\n• 5 years with BS/BA...   
6     None VA US  Job Description\n• ACTIVE TS/SCI WITH FULL SCO...   
13    None VA US  Job Description:\n\nIMS Consulting is looking ...   
..           ...                                                ...   
344   None MD US  At General Dynamics Information Technology (GD...   
396   None CA US  Are you a skilled web developer with a passion...   
407   None WA US  Angular 2+ Developer:\nClient is looking for a...   
409   None PA US  As the largest online distributor of restauran...   
419   None TX US  Position : UI Developer\nLocation : Plano, TX\...   

                         Year  Salary  Experience             Job Group  
0    2024-11-22T00:00:00.000Z     NaN           6                 Other  
1                         NaN     NaN           0                 Other  
3    2024-10-23T00:00:00.000Z     NaN           5          Data Science  
6                         NaN     NaN          11  Software Development  
13                        NaN     NaN           2                 Other  
..                        ...     ...         ...                   ...  
344  2024-11-08T00:00:00.000Z     NaN           5                 Other  
396  2024-11-19T00:00:00.000Z     NaN           5       Web Development  
407  2024-11-20T00:00:00.000Z     NaN           7                 Other  
409  2024-11-11T00:00:00.000Z     NaN           4                 Other  
419                       NaN     NaN           0                 Other  

[110 rows x 11 columns]

Số năm kinh nghiệm quy định bất thường 15 trở lên

In [2]:
import numpy as np

In [135]:
df.loc[df['Experience'] > 15, 'Experience'] = np.nan

In [136]:
df['date'] = pd.to_datetime(df['Year'])

df['Year'] = df['date'].dt.year

In [137]:
df.to_csv('data_cleaned.csv', index=False)

In [7]:
print(df)

                                             Job Title  Job Score  \
0                                  .Net Developer Jobs        NaN   
1                                       .NET Developer        NaN   
2                          MS Power Platform Developer        NaN   
3                            Data Developer/ Team Lead        NaN   
4                   CBT Developer w active TS/SCI Poly        NaN   
..                                                 ...        ...   
207  C#.NET Developer w/ React Exp (Mid-Sr) - Remot...        NaN   
208                           Web Developer I - 525281        NaN   
209  Adjunct Faculty Non-Instructional Course Devel...        NaN   
210  Developer in Test II - Core Enterprise Data an...        NaN   
211                           UI Developer - Plano, TX        NaN   

    Job Experience Required  Postgraduate degree Job Skills Required  \
0             Not Available                False       Not Available   
1             Not Available

In [8]:
# Xử lý cột 'Postgraduate degree' để thành giá trị số
df['Postgraduate degree'] = df['Postgraduate degree'].astype(int)

# Xử lý cột 'Job Experience Required'
# Giả sử 'Not Available' có thể thay bằng 0 năm kinh nghiệm
df['Job Experience Required'] = df['Job Experience Required'].apply(lambda x: 0 if x == 'Not Available' else int(x))

# Giả sử cột 'Job Skills Required' có thể được mã hóa vào các giá trị số
df['Job Skills Required'] = df['Job Skills Required'].apply(lambda x: 0 if x == 'Not Available' else 1)  # Giả định


In [13]:
df = df.drop('Job Score', axis = 1)
df = df.drop('Job Location', axis = 1)

In [14]:

skills_keywords = ['Python', 'C#', 'SQL', 'React', 'JavaScript', 'Data Science', 'Power BI', 'PowerApps', 'Machine Learning']

def extract_skills(description):
    found_skills = []
    for skill in skills_keywords:
        if skill.lower() in description.lower():  
            found_skills.append(skill)
    return found_skills

df['Job Skills Required'] = df['Job Description'].apply(extract_skills)

In [19]:

df = df.drop('date',axis =1)

In [22]:
df = df.drop('Job Experience Required', axis = 1)

In [27]:
df = df.drop('Postgraduate degree', axis = 1)

In [25]:
education_keywords = ['Bachelor\'s', 'Master\'s', 'PhD', 'Doctorate', 'Degree', 'Associate']

# Hàm để trích xuất trình độ học vấn
def extract_education_level(description):
    for degree in education_keywords:
        if degree.lower() in description.lower():  # Tìm kiếm không phân biệt chữ hoa và chữ thường
            return degree
    return 'Not Available'  # Trường hợp không tìm thấy

# Áp dụng hàm lên cột 'Job Description'
df['Education Level'] = df['Job Description'].apply(extract_education_level)

levels_keywords = ['Junior', 'Mid', 'Senior', 'Lead', 'Entry', 'Principal', 'Executive']

# Hàm để trích xuất trình độ công việc
def extract_job_level(description):
    for level in levels_keywords:
        if level.lower() in description.lower():  # Tìm kiếm không phân biệt chữ hoa và chữ thường
            return level
    return 'Not Available'  # Trường hợp không tìm thấy

# Áp dụng hàm lên cột 'Job Description'
df['Job Level'] = df['Job Description'].apply(extract_job_level)
df

Job Title  Postgraduate degree  \
0                                  .Net Developer Jobs                    0   
1                                       .NET Developer                    0   
2                          MS Power Platform Developer                    0   
3                            Data Developer/ Team Lead                    0   
4                   CBT Developer w active TS/SCI Poly                    0   
..                                                 ...                  ...   
207  C#.NET Developer w/ React Exp (Mid-Sr) - Remot...                    0   
208                           Web Developer I - 525281                    0   
209  Adjunct Faculty Non-Instructional Course Devel...                    0   
210  Developer in Test II - Core Enterprise Data an...                    0   
211                           UI Developer - Plano, TX                    0   

                     Job Skills Required  \
0                           [JavaScript]   
1                              [C#, SQL]   
2                     [Python, Power BI]   
3                          [Python, SQL]   
4                                     []   
..                                   ...   
207              [C#, React, JavaScript]   
208             [SQL, React, JavaScript]   
209                                   []   
210  [Python, SQL, JavaScript, Power BI]   
211                  [React, JavaScript]   

                                       Job Description    Salary  Experience  \
0    Client is seeking a senior-mid level .Net deve...       NaN         6.0   
1    As the .NET Developer you will be apart of a t...       NaN         0.0   
2    Description\n\nLeidos currently has an opening...   81250.0         4.0   
3    Required Qualifications:\n• 5 years with BS/BA...       NaN         5.0   
4    Description\n\nLooking for a rewarding career ...   78000.0         8.0   
..                                                 ...       ...         ...   
207  As the largest online distributor of restauran...       NaN         4.0   
208  Pay Grade/Pay Range: Minimum: $48,600 - Midpoi...   48600.0         0.0   
209  Adjunct Faculty Non-Instructional Course Devel...   68000.0         0.0   
210  Company Description\n\n“We’re not in the shipp...  100000.0         4.0   
211  Position : UI Developer\nLocation : Plano, TX\...       NaN         0.0   

           Job Group      Job Level Education Level  
0              Other            Mid        Master's  
1              Other  Not Available   Not Available  
2              Other  Not Available          Degree  
3       Data Science         Senior             PhD  
4              Other  Not Available          Degree  
..               ...            ...             ...  
207            Other            Mid       Associate  
208  Web Development            Mid      Bachelor's  
209            Other            Mid      Bachelor's  
210     Data Science           Lead   Not Available  
211            Other  Not Available   Not Available  

[212 rows x 9 columns]

In [29]:
df

Job Title  \
0                                  .Net Developer Jobs   
1                                       .NET Developer   
2                          MS Power Platform Developer   
3                            Data Developer/ Team Lead   
4                   CBT Developer w active TS/SCI Poly   
..                                                 ...   
207  C#.NET Developer w/ React Exp (Mid-Sr) - Remot...   
208                           Web Developer I - 525281   
209  Adjunct Faculty Non-Instructional Course Devel...   
210  Developer in Test II - Core Enterprise Data an...   
211                           UI Developer - Plano, TX   

                     Job Skills Required  \
0                           [JavaScript]   
1                              [C#, SQL]   
2                     [Python, Power BI]   
3                          [Python, SQL]   
4                                     []   
..                                   ...   
207              [C#, React, JavaScript]   
208             [SQL, React, JavaScript]   
209                                   []   
210  [Python, SQL, JavaScript, Power BI]   
211                  [React, JavaScript]   

                                       Job Description    Salary  Experience  \
0    Client is seeking a senior-mid level .Net deve...       NaN         6.0   
1    As the .NET Developer you will be apart of a t...       NaN         0.0   
2    Description\n\nLeidos currently has an opening...   81250.0         4.0   
3    Required Qualifications:\n• 5 years with BS/BA...       NaN         5.0   
4    Description\n\nLooking for a rewarding career ...   78000.0         8.0   
..                                                 ...       ...         ...   
207  As the largest online distributor of restauran...       NaN         4.0   
208  Pay Grade/Pay Range: Minimum: $48,600 - Midpoi...   48600.0         0.0   
209  Adjunct Faculty Non-Instructional Course Devel...   68000.0         0.0   
210  Company Description\n\n“We’re not in the shipp...  100000.0         4.0   
211  Position : UI Developer\nLocation : Plano, TX\...       NaN         0.0   

           Job Group      Job Level Education Level  
0              Other            Mid        Master's  
1              Other  Not Available   Not Available  
2              Other  Not Available          Degree  
3       Data Science         Senior             PhD  
4              Other  Not Available          Degree  
..               ...            ...             ...  
207            Other            Mid       Associate  
208  Web Development            Mid      Bachelor's  
209            Other            Mid      Bachelor's  
210     Data Science           Lead   Not Available  
211            Other  Not Available   Not Available  

[212 rows x 8 columns]

In [41]:
df.to_csv('data_cleaned.csv', index = False)

In [42]:
df = pd.read_csv('data_cleaned.csv')

In [43]:
df

Job Title  \
0                                  .Net Developer Jobs   
1                                       .NET Developer   
2                          MS Power Platform Developer   
3                            Data Developer/ Team Lead   
4                   CBT Developer w active TS/SCI Poly   
..                                                 ...   
207  C#.NET Developer w/ React Exp (Mid-Sr) - Remot...   
208                           Web Developer I - 525281   
209  Adjunct Faculty Non-Instructional Course Devel...   
210  Developer in Test II - Core Enterprise Data an...   
211                           UI Developer - Plano, TX   

                             Job Skills Required  \
0                                 ['JavaScript']   
1                                  ['C#', 'SQL']   
2                         ['Python', 'Power BI']   
3                              ['Python', 'SQL']   
4                                             []   
..                                           ...   
207                ['C#', 'React', 'JavaScript']   
208               ['SQL', 'React', 'JavaScript']   
209                                           []   
210  ['Python', 'SQL', 'JavaScript', 'Power BI']   
211                      ['React', 'JavaScript']   

                                       Job Description    Salary  Experience  \
0    Client is seeking a senior-mid level .Net deve...       NaN         6.0   
1    As the .NET Developer you will be apart of a t...       NaN         0.0   
2    Description\n\nLeidos currently has an opening...   81250.0         4.0   
3    Required Qualifications:\n• 5 years with BS/BA...       NaN         5.0   
4    Description\n\nLooking for a rewarding career ...   78000.0         8.0   
..                                                 ...       ...         ...   
207  As the largest online distributor of restauran...       NaN         4.0   
208  Pay Grade/Pay Range: Minimum: $48,600 - Midpoi...   48600.0         0.0   
209  Adjunct Faculty Non-Instructional Course Devel...   68000.0         0.0   
210  Company Description\n\n“We’re not in the shipp...  100000.0         4.0   
211  Position : UI Developer\nLocation : Plano, TX\...       NaN         0.0   

                Job Group      Job Level Education Level  
0    Software Development            Mid        Master's  
1    Software Development  Not Available   Not Available  
2    Software Development  Not Available          Degree  
3            Data Science         Senior             PhD  
4    Software Development  Not Available          Degree  
..                    ...            ...             ...  
207  Software Development            Mid       Associate  
208       Web Development            Mid      Bachelor's  
209  Software Development            Mid      Bachelor's  
210          Data Science           Lead   Not Available  
211  Software Development  Not Available   Not Available  

[212 rows x 8 columns]

Xử lý những Salary bất thường/vô lý

Phân tích độ dài thích hợp cho dữ liệu

Xử lý dữ liệu thiếu